In [1]:
%load_ext pyinstrument

In [2]:
import sys
sys.path.append('/mnt/d/packing/code/core/')
import kaggle_support as kgs
import importlib
import matplotlib.pyplot as plt
importlib.reload(kgs)

local
local


<module 'kaggle_support' from '/mnt/d/packing/code/core/kaggle_support.py'>

In [3]:
import pack_basics
import pack_vis
importlib.reload(pack_basics)
importlib.reload(pack_vis)
tree_list = pack_basics.place_random(150, 5)
#tree_list.xyt = [[0.,0.,0.],[0.,1.,np.pi]]
#pack_vis.visualize_tree_list(tree_list)

import pack_cost
import numpy as np
import cupy as cp
from matplotlib import animation
from IPython.display import HTML
cost = pack_cost.PackingCost()
cost.collision_cost = pack_cost.CollisionCostOverlappingArea()

N_steps = 400
dt = 0.02
xyt_list = cp.zeros((N_steps, tree_list.N, 3))
xyt = cp.array(tree_list.xyt)
%pyinstrument total_cost, total_grad = cost.compute_total_cost(cp.array(tree_list.xyt), include_gradients=True)
for i_step in range(N_steps):
    xyt_list[i_step] = xyt
    total_cost, total_grad = cost.compute_total_cost(xyt, include_gradients=True)
    xyt -= dt * total_grad
    if (i_step)%10==0:
        print(i_step)
        # tree_list.xyt=xyt
        # pack_vis.visualize_tree_list(tree_list)
        # plt.title(f'{i_step}, {total_cost}')
        # plt.pause(0.001)


#pack_vis.visualize_tree_list(tree_list)



_     ._   __/__   _ _  _  _ _/_   Recorded: 07:55:47  Samples:  8
 /_//_/// /_\ / //_// / //_'/ //     Duration: 0.023     CPU time: 0.020
/   _/                      v5.1.1

Line in cell [3]

0.022 <cell line: 0>  /tmp/ipykernel_5352/2368197407.py:1
`- 0.022 PackingCost.compute_total_cost  pack_cost.py:103
   `- 0.022 CollisionCostOverlappingArea.compute_cost  <decorator-gen-120>:1
      `- 0.022 profile_each_line  kaggle_support.py:142
         `- 0.022 CollisionCostOverlappingArea.compute_cost  pack_cost.py:42
            `- 0.022 overlap_list_total  pack_cuda.py:616
               |- 0.021 _ensure_initialized  pack_cuda.py:538
               |  |- 0.018 _compile_module_with_cache  cupy/cuda/compiler.py:517
               |  |     [26 frames hidden]  cupy, importlib, email, <built-in>, <...
               |  |        0.015 compileProgram  <built-in>
               |  |- 0.003 _get_include_dir_from_conda_or_wheel  cupy/_environment.py:455
               |  |     [10 frames hidden]  importlib, <built-in>
               |  `- 0.001 [self]  pack_cuda.py
               `- 0.001 ascontiguousarray  cupy/_creation/from_data.py:105
                     [2 frames hidden]  cupy

0
10
20
30
40
50
60
70
80
90
100
110
120
130
140
150
160
170
180
190
200
210
220
230
240
250
260
270
280
290
300
310
320
330
340
350
360
370
380
390


In [4]:
importlib.reload(pack_vis)

# compute fixed axis limits from the last frame (convert from cupy to numpy)
last = cp.asnumpy(xyt_list[-1])
minx, maxx = last[:, 0].min(), last[:, 0].max()
miny, maxy = last[:, 1].min(), last[:, 1].max()
dx, dy = maxx - minx, maxy - miny
pad = 0.1 * max(dx, dy, 1e-3)  # small epsilon to avoid zero padding
xlim = (minx - pad, maxx + pad)
ylim = (miny - pad, maxy + pad)

fig, ax = plt.subplots(figsize=(10, 10))

def animate(i):
    ax.clear()
    ax.set_xlim(*xlim)
    ax.set_ylim(*ylim)
    ax.set_aspect('equal', adjustable='box')
    tree_list.xyt = xyt_list[i]
    pack_vis.visualize_tree_list(tree_list, ax=ax)
    ax.set_xlim(*xlim)
    ax.set_ylim(*ylim)
    ax.set_title(f'Step {i}/{N_steps-1}')

anim = animation.FuncAnimation(fig, animate, frames=np.round(np.linspace(0, N_steps-1, 20)).astype(int), interval=100)
plt.close()
HTML(anim.to_jshtml())